In [2]:
!pip install gradio
!pip install nltk
!pip install scipy
!pip install torch
!pip install transformers
!pip install tokenizers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 55.7 MB/s eta 0:00:0000:01m0:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.7/318.7 kB 16.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.3/10.3 MB 68.5 MB/s eta 0:00:00:00:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.4/121.4 kB 7.2 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.26.18
    Uninstalling urllib3-1.26.18:
      Successfully uninstalled urllib3-1.26.18
  Attempting uninstall: tomlkit
    Found existing installation: tomlkit 0.13.2
    Uninstalling tomlkit-0.13.2:
      Successfully uninstalled tomlkit-0.13.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
distributed 2024.7.1 requires dask==2024.7.1, but you have dask 2024.8.1 which is incompatible.
kfp 2.5.0 requires google-cloud-storage<3,>=2.2.1, but you have googl

In [ ]:
!git clone https://github.com/jwkirchenbauer/lm-watermarking.git

In [9]:

# Add the directory containing the script to the Python path
sys.path.insert(0, str(Path("/kaggle/working/lm-watermarking").resolve()))

In [10]:
import numpy as np 
import pandas as pd 
import sys
import os
from transformers import T5Tokenizer, T5ForConditionalGeneration, LogitsProcessorList
from datasets import load_dataset
import sys
from pathlib import Path
from tqdm import tqdm
from huggingface_hub import login
from datasets import Dataset, DatasetDict
from datetime import datetime
from transformers import T5Tokenizer, T5ForConditionalGeneration, LogitsProcessorList
from extended_watermark_processor import WatermarkLogitsProcessor

In [11]:
!pwd

/kaggle/working


In [12]:
input_text = """
The full cost of damage in Newton Stewart, one of the areas worst affected, is still being assessed. Repair work is ongoing in Hawick and many roads in Peeblesshire remain badly affected by standing water. Trains on the west coast mainline face disruption due to damage at the Lamington Viaduct. Many businesses and householders were affected by flooding in Newton Stewart after the River Cree overflowed into the town. First Minister Nicola Sturgeon visited the area to inspect the damage. The waters breached a retaining wall, flooding many commercial properties on Victoria Street - the main shopping thoroughfare. Jeanette Tate, who owns the Cinnamon Cafe which was badly affected, said she could not fault the multi-agency response once the flood hit. However, she said more preventative work could have been carried out to ensure the retaining wall did not fail. "It is difficult but I do think there is so much publicity for Dumfries and the Nith - and I totally appreciate that - but it is almost like we're neglected or forgotten," she said. "That may not be true but it is perhaps my perspective over the last few days. "Why were you not ready to help us a bit more when the warning and the alarm alerts had gone out?" Meanwhile, a flood alert remains in place across the Borders because of the constant rain. Peebles was badly hit by problems, sparking calls to introduce more defences in the area. Scottish Borders Council has put a list on its website of the roads worst affected and drivers have been urged not to ignore closure signs. The Labour Party's deputy Scottish leader Alex Rowley was in Hawick on Monday to see the situation first hand. He said it was important to get the flood protection plan right but backed calls to speed up the process. "I was quite taken aback by the amount of damage that has been done," he said. "Obviously it is heart-breaking for people who have been forced out of their homes and the impact on businesses." He said it was important that "immediate steps" were taken to protect the areas most vulnerable and a clear timetable put in place for flood prevention plans. Have you been affected by flooding in Dumfries and Galloway or the Borders? Tell us about your experience of the situation and how it was handled. Email us on selkirk.news@bbc.co.uk or dumfries@bbc.co.uk.
"""

In [18]:


# Load the tokenizer and model
tokenizer = T5Tokenizer.from_pretrained("google/flan-t5-small")
model = T5ForConditionalGeneration.from_pretrained("google/flan-t5-small")


# Create an instance of the WatermarkLogitsProcessor
watermark_processor = WatermarkLogitsProcessor(
    vocab=list(tokenizer.get_vocab().values()),
    gamma=0.5,
    delta=2.0,
    seeding_scheme="simple_1"
)


print(input_text)
print("*"*50)
# Tokenize the input text
tokenized_input = tokenizer(input_text, return_tensors='pt', padding=True).to(model.device)


# Generate the output tokens with the watermark logits processor
output_tokens = model.generate(
    input_ids=tokenized_input['input_ids'],
    logits_processor=LogitsProcessorList([watermark_processor]),
    max_length=500,  # Increase this value as needed
    min_length=100,
    num_beams=4,     # Use beam search with 5 beams
    early_stopping=True,  # Stop early when all beams reach the end token
    temperature=0.5,  # Control creativity (lower is more conservative)
    top_p=0.5,         # Nucleus sampling
    diversity_penalty=0.5,
    num_beam_groups=2
)

# Decode the output tokens to get the generated text
generated_text = tokenizer.batch_decode(output_tokens, skip_special_tokens=True)
print(generated_text[0])

Token indices sequence length is longer than the specified maximum sequence length for this model (539 > 512). Running this sequence through the model will result in indexing errors



The full cost of damage in Newton Stewart, one of the areas worst affected, is still being assessed. Repair work is ongoing in Hawick and many roads in Peeblesshire remain badly affected by standing water. Trains on the west coast mainline face disruption due to damage at the Lamington Viaduct. Many businesses and householders were affected by flooding in Newton Stewart after the River Cree overflowed into the town. First Minister Nicola Sturgeon visited the area to inspect the damage. The waters breached a retaining wall, flooding many commercial properties on Victoria Street - the main shopping thoroughfare. Jeanette Tate, who owns the Cinnamon Cafe which was badly affected, said she could not fault the multi-agency response once the flood hit. However, she said more preventative work could have been carried out to ensure the retaining wall did not fail. "It is difficult but I do think there is so much publicity for Dumfries and the Nith - and I totally appreciate that - but it is a

In [21]:
# Load the EdinburghNLP/xsum dataset
dataset = load_dataset("EdinburghNLP/xsum")


Generating train split:   0%|          | 0/204045 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/11332 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11334 [00:00<?, ? examples/s]

In [13]:
# Load the tokenizer and model
# google/flan-t5-small
# google-t5/t5-small
# google/mt5-small
tokenizer = T5Tokenizer.from_pretrained("google-t5/t5-small")
model = T5ForConditionalGeneration.from_pretrained("google-t5/t5-small")

# Create an instance of the WatermarkLogitsProcessor
watermark_processor = WatermarkLogitsProcessor(
    vocab=list(tokenizer.get_vocab().values()),
    gamma=0.5,
    delta=2.0,
    seeding_scheme="simple_1"
)

def watermark_summary(summary):
    # Tokenize the summary
    tokenized_input = tokenizer(summary, return_tensors='pt', padding=True).to(model.device)
    
    # Generate the output tokens with the watermark logits processor
    output_tokens = model.generate(
        input_ids=tokenized_input['input_ids'],
        logits_processor=LogitsProcessorList([watermark_processor]),
        max_length=30,  # Increase this value as needed
        min_length=20,
        num_beams=4,     # Use beam search with 4 beams
        early_stopping=True,  # Stop early when all beams reach the end token
        temperature=0.5,  # Control creativity (lower is more conservative)
        top_p=0.5,        # Nucleus sampling
        diversity_penalty=0.5,
        num_beam_groups=2
    )
    
    # Decode the output tokens to get the generated text
    generated_text = tokenizer.batch_decode(output_tokens, skip_special_tokens=True)
    return generated_text[0]

tokenizer_config.json:   0%|          | 0.00/2.32k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/242M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

In [22]:
# Take the first 1000 samples from the test set
subset_test = dataset['test'].select(range(10000))

# Print the subset to confirm
print(subset_test)

Dataset({
    features: ['document', 'summary', 'id'],
    num_rows: 10000
})


In [23]:
subset_test

Dataset({
    features: ['document', 'summary', 'id'],
    num_rows: 10000
})

In [14]:
# Log in to your Hugging Face account
login(token="put your token here")

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: fineGrained).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [25]:
# Define a base name for your repository
repo_name = "youssefkhalil320/xsum-watermarked-flan-t5-small"

# Initialize an empty list for watermarked summaries
watermarked_summaries = []

# Process the dataset in batches
for i, record in enumerate(tqdm(subset_test, desc="Watermarking Summaries"), 1):
    print(record["summary"])
    watermarked_summary = watermark_summary(record["summary"])
    watermarked_summaries.append(watermarked_summary)

    # Process every 100 records
    if i % 100 == 0 or i == len(subset_test):
        print(f"Pushing to index {i} to the hub")
        # Create a temporary dataset for the current batch
        temp_dataset = Dataset.from_dict({
            "document": subset_test["document"][:i],
            "summary": subset_test["summary"][:i],
            "watermarked_summary": watermarked_summaries
        })

        # Push the temporary dataset to the Hugging Face Hub
        version = datetime.now().strftime("%Y%m%d%H%M%S")
        print(f"to index {i} done on {version}")
        dataset_name = f"{repo_name}"
        temp_dataset.push_to_hub(dataset_name)
        

# Handle remaining summaries
if watermarked_summaries:
    temp_dataset = Dataset.from_dict({
        "document": subset_test["document"],
        "summary": subset_test["summary"],
        "watermarked_summary": watermarked_summaries
    })
    
    dataset_name = f"{repo_name}"
    temp_dataset.push_to_hub(dataset_name)

Watermarking Summaries:   0%|          | 0/10000 [00:00<?, ?it/s]/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:567: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.5` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:572: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.5` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


There is a "chronic" need for more housing for prison leavers in Wales, according to a charity.


Watermarking Summaries:   0%|          | 1/10000 [00:02<7:50:42,  2.82s/it]

A man has appeared in court after firearms, ammunition and cash were seized by police in Edinburgh.


Watermarking Summaries:   0%|          | 2/10000 [00:05<7:44:18,  2.79s/it]

...

Watermarking Summaries: 100%|██████████| 10000/10000 [8:07:31<00:00,  2.93s/it]


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/366 [00:00<?, ?B/s]

No files have been modified since last commit. Skipping to prevent empty commit.


In [15]:
# Load the EdinburghNLP/xsum dataset
dataset = load_dataset("abisee/cnn_dailymail", '1.0.0')


Generating train split:   0%|          | 0/287113 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/13368 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11490 [00:00<?, ? examples/s]

In [16]:
# Take the first 1000 samples from the test set
subset_test = dataset['test'].select(range(10000))

# Print the subset to confirm
print(subset_test)

Dataset({
    features: ['article', 'highlights', 'id'],
    num_rows: 10000
})


In [17]:
# Define a base name for your repository
repo_name = "youssefkhalil320/cnn_dailymail-watermarked-t5-small"

# Initialize an empty list for watermarked summaries
watermarked_summaries = []

# Process the dataset in batches
for i, record in enumerate(tqdm(subset_test, desc="Watermarking Summaries"), 1):
    print(record["highlights"])
    watermarked_summary = watermark_summary(record["highlights"])
    watermarked_summaries.append(watermarked_summary)

    # Process every 100 records
    if i % 100 == 0 or i == len(subset_test):
        print(f"Pushing to index {i} to the hub")
        # Create a temporary dataset for the current batch
        temp_dataset = Dataset.from_dict({
            "document": subset_test["article"][:i],
            "summary": subset_test["highlights"][:i],
            "watermarked_summary": watermarked_summaries
        })

        # Push the temporary dataset to the Hugging Face Hub
        version = datetime.now().strftime("%Y%m%d%H%M%S")
        print(f"to index {i} done on {version}")
        dataset_name = f"{repo_name}"
        temp_dataset.push_to_hub(dataset_name)
        

# Handle remaining summaries
if watermarked_summaries:
    temp_dataset = Dataset.from_dict({
        "document": subset_test["article"],
        "summary": subset_test["highlights"],
        "watermarked_summary": watermarked_summaries
    })
    
    dataset_name = f"{repo_name}"
    temp_dataset.push_to_hub(dataset_name)

Watermarking Summaries:   0%|          | 0/10000 [00:00<?, ?it/s]/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:567: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.5` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:572: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.5` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Membership gives the ICC jurisdiction over alleged crimes committed in Palestinian territories since last June . Israel and the United States opposed the move, which could open the door to war crimes investigations against Israelis .


Watermarking Summaries:   0%|          | 1/10000 [00:01<3:12:32,  1.16s/it]

Theia, a bully breed mix, was apparently hit by a car, whacked with a hammer and buried in a field . "She's a true miracle dog and she deserves a good life," says Sara Mellado, who is looking for a home for Theia .


Watermarking Summaries:   0%|          | 2/10000 [00:02<3:08:31,  1.13s/it]

...

Watermarking Summaries: 100%|██████████| 10000/10000 [3:07:08<00:00,  1.12s/it]


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/10 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/366 [00:00<?, ?B/s]

No files have been modified since last commit. Skipping to prevent empty commit.
